In [2]:
import nltk
import matplotlib.pyplot as plt
from nltk.corpus import gutenberg as gb
from nltk.util import pad_sequence
from nltk.util import bigrams
from nltk.util import ngrams
from nltk.util import everygrams
from nltk.lm.preprocessing import pad_both_ends
from nltk.lm.preprocessing import flatten
from nltk import word_tokenize, sent_tokenize 
import pandas as pd

古腾堡语料库 NLTK包含古腾堡项目（Project Gutenberg）电子文档的一小部分文本。 该项目大约有25000（现在是36000）本免费电子书。 我们通过平均句子长度和平均词种数（词语丰富度）这两个特征，来看不同作者的写作风格。

NLTK的古腾堡语料库收集的都是不同作家的书

In [3]:
nltk.download('gutenberg')
nltk.download('punkt')
nltk.download('movie_reviews')#电影评论
nltk.download('webtext') #网络和聊天文本
from nltk.corpus import gutenberg
from nltk.corpus import webtext
from nltk.corpus import movie_reviews
#print(gutenberg.fileids())
hamlet = gutenberg.words('shakespeare-hamlet.txt')  # 获取shakespeare-hamlet.txt这个文件的单词
print(hamlet)
hamlets = gutenberg.sents('shakespeare-hamlet.txt')  # 获取shakespeare-hamlet.txt这个文件的句子
print(hamlets)
send_table = [] # 得到text的二维str数组
text_string = '' # text纯string表示
p = ''',.";:'?()[]!`'''
data_source = movie_reviews
for text_id in data_source.fileids():
    unit = data_source.sents(text_id)
    for s in unit:
        sent = []
        sent.append('<s')
        for word in s:
            if len(word)==1 and word in p:
                continue #在此增加if条件可以去除停用词等
            word = word.lower()
            sent.append(word)
            text_string+=word+' '
        sent.append('/s>')
        send_table.append(sent)

[nltk_data] Downloading package gutenberg to /home/wofei/nltk_data...
[nltk_data]   Package gutenberg is already up-to-date!
[nltk_data] Downloading package punkt to /home/wofei/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package movie_reviews to
[nltk_data]     /home/wofei/nltk_data...
[nltk_data]   Package movie_reviews is already up-to-date!
[nltk_data] Downloading package webtext to /home/wofei/nltk_data...
[nltk_data]   Package webtext is already up-to-date!


['[', 'The', 'Tragedie', 'of', 'Hamlet', 'by', ...]
[['[', 'The', 'Tragedie', 'of', 'Hamlet', 'by', 'William', 'Shakespeare', '1599', ']'], ['Actus', 'Primus', '.'], ...]


In [ ]:
try: # Use the default NLTK tokenizer.
    from nltk import word_tokenize, sent_tokenize 
    # Testing whether it works. 
    # Sometimes it doesn't work on some machines because of setup issues.
    word_tokenize(sent_tokenize("This is a foobar sentence. Yes it is.")[0])
except: # Use a naive sentence tokenizer and toktok.
    import re
    from nltk.tokenize import ToktokTokenizer
    # See https://stackoverflow.com/a/25736515/610569
    sent_tokenize = lambda x: re.split(r'(?<=[^A-Z].[.?]) +(?=[A-Z])', x)
    # Use the toktok tokenizer that requires no dependencies.
    toktok = ToktokTokenizer()
    word_tokenize = word_tokenize = toktok.tokenize

In [ ]:
import os
import requests
import io #codecs


# Text version of https://kilgarriff.co.uk/Publications/2005-K-lineer.pdf
if os.path.isfile('language-never-random.txt'):
    with io.open('language-never-random.txt', encoding='utf8') as fin:
        text = fin.read()
else:
    url = "https://gist.githubusercontent.com/alvations/53b01e4076573fea47c6057120bb017a/raw/b01ff96a5f76848450e648f35da6497ca9454e4a/language-never-random.txt"
    text = requests.get(url).content.decode('utf8')
    with io.open('language-never-random.txt', 'w', encoding='utf8') as fout:
        fout.write(text)

In [ ]:
# Tokenize the text.
tokenized_text = [list(map(str.lower, word_tokenize(sent))) 
                  for sent in sent_tokenize(text)]

In [4]:
import string
sent_t = []
for w_l in tokenized_text:
    sent_t.append(' '.join(w_l).replace(',','').replace('- ','').replace('.','').replace('  ',' '))
d = {'sentence':sent_t}
sent_table = pd.DataFrame(d)
sent_list = []
for sent in sent_table['sentence']:
    w_list = []
    for word in sent.split(' '):
        w_list.append(str(word))
    sent_list.append(w_list)
sent_table.head()

NameError: name 'tokenized_text' is not defined

In [5]:
word_list =[n for a in send_table for n in a]
word_set=set(word_list)

In [6]:
# 对text_string进行词频统计
word_list = []
cnt_list = []
text_tokenized = nltk.word_tokenize(text_string)
#print(text_tokenized)   
from nltk import FreqDist
fdist = FreqDist(text_tokenized)
print(fdist)
for a,b in fdist.items():
    word_list.append(str(a))
    cnt_list.append(b)
dic = {
    'word':word_list,
    'cnt':cnt_list
}
info_table = pd.DataFrame(dic)
info_table.head(10)

<FreqDist with 39732 samples and 1358059 outcomes>


word    cnt
0     plot   1513
1      two   1911
2     teen    151
3  couples     27
4       go   1113
5       to  31937
6        a  38106
7   church     69
8    party    183
9    drink     32

In [7]:
# Preprocess the tokenized text for 3-grams language modelling
# send_table: list[list(str)]
from nltk.lm.preprocessing import padded_everygram_pipeline
n = 3
train_data, padded_sents = padded_everygram_pipeline(n, send_table)

In [8]:
# 使用nltk 的ngram模型
from nltk.lm import MLE
model = MLE(n) # Lets train a 3-grams model, previously we set n=3

In [9]:
model.fit(train_data, padded_sents)
print(model.vocab)

<Vocabulary with cutoff=1 unk_label='<UNK>' and 39760 items>


In [66]:
model.logscore('william',['hamlet','by'])

-inf

In [54]:
word2sum = {}
word_set = set()
for sent in send_table:
    w1=''
    w2=''
    for word in sent:
        if w2 == '':
            log_prob = -model.logscore(word)
        elif w1 == '':
            log_prob = -model.logscore(word,[w2])
        else:
            log_prob = -model.logscore(word,[w1,w2])
        print(log_prob)
        if word in word2sum:
            word2sum[word] += log_prob
        else:
            word2sum[word] = 0
        w1 = w2
        w2 = word

4.224109694042735
13.65105169117893
1.0
3.5849625007211565
-0.0
9.27262978497637
1.5849625007211563
-0.0
1.0
-0.0
-0.0
-0.0
-0.0
3.4594316186372978
-0.0
1.0
-0.0
-0.0
1.3219280948873622
1.5849625007211563
1.222392421336448
0.09310940439148148
1.0780025120012733
4.247927513443586
-0.0
2.0
5.7279204545632
2.0
-0.0
2.0
1.2515387669959643
5.54432051622381
3.1699250014423126
2.584962500721156
3.321928094887362
-0.0
2.4594316186372973
3.700439718141092
1.3219280948873622
1.0
1.5849625007211563
-0.0
2.321928094887362
-0.0
6.6865005271832185
-0.0
-0.0
-0.0
2.8579809951275723
1.3219280948873622
6.599912842187128
2.8073549220576046
2.8073549220576046
2.0
-0.0
2.321928094887362
-0.0
3.0
2.321928094887362
-0.0
-0.0
-0.0
4.224109694042735
13.65105169117893
1.0
-0.0
-0.0
-0.0
4.523561956057013
-0.0
2.9068905956085187
4.224109694042735
13.65105169117893
1.0
1.0
-0.0
-0.0
-0.0
2.8073549220576046
1.5849625007211563
1.0
2.0
-0.0
2.8073549220576046
1.0
-0.0
2.8073549220576046
-0.0
6.1765887317233235
1.58

In [55]:
#增加词长、计算信息量
word_count_table = pd.DataFrame()
for n,word in enumerate(info_table['word']):
    # Create a list of just the word we are interested in, we use regular expressions so that part of words do not count
    # e.g. 'ear' would be counted in each appearance of the word 'year'
    word_count = len(word)  
    word_count_table = word_count_table.append(pd.DataFrame({'len':word_count}, index=[n]))
info_table['len'] = word_count_table['len']
sum_table = pd.DataFrame()
for n,word in enumerate(info_table['word']):
    if word not in word2sum:
        sum_table = sum_table.append(pd.DataFrame({'sum':-1}, index=[n]))
        continue
    sum_proc = word2sum[word]
    sum_table = sum_table.append(pd.DataFrame({'sum':sum_proc}, index=[n]))
info_table['sum_neg_log_prob'] = sum_table['sum']
info_table['averge_content'] = (info_table['sum_neg_log_prob']/info_table['cnt'])
info_table.head(30)

word   cnt  len  sum_neg_log_prob  averge_content
0     cookie    66    6        130.787873        1.981634
1    manager   420    7        386.749929        0.920833
2        don  1241    3       3939.904245        3.174782
3          t  3547    1        510.741598        0.143993
4      allow    72    5        233.603540        3.244494
5      sites    67    5        111.291077        1.661061
6       that  2792    4       7431.841985        2.661835
7        set   159    3        431.303675        2.712602
8    removed    27    7         66.279907        2.454811
9    cookies    82    7        124.205295        1.514699
10        to  6325    2       6745.793983        1.066529
11    future    17    6         76.903436        4.523732
12    should   681    6       1592.173941        2.337994
13      stay    56    4        247.134117        4.413109
14   checked    26    7         77.225497        2.970211
15      when  1833    4       3228.409895        1.761271
16        in  4293    2       6417.741725        1.494932
17      full    94    4        226.238730        2.406795
18    screen   125    6        199.288631        1.594309
19      mode    57    4         66.466400        1.166077
20  pressing    28    8         88.788320        3.171011
21      ctrl   171    4        373.289310        2.182978
22         -  3441    1       2476.316446        0.719650
23         n    62    1        128.995795        2.080577
24      open   679    4       1827.746882        2.691822
25         a  6199    1      12483.805132        2.013842
26       new   790    3       1969.604384        2.493170
27   browser   484    7        886.698149        1.832021
28      only   366    4       1243.936518        3.398734
29  download   442    8       1062.220018        2.403213

In [1]:
info_table_14 = info_table[info_table['len']<15]
info_table_14.plot.scatter(x="len", y="averge_content",alpha=0.03)
plt.savefig('./webtext_ALL_300dpi.jpg', bbox_inches='tight', dpi=300)
info_table.sort_values(by='len',ascending='False')
long_word = list(info_table[info_table['len']>10]['word'])

NameError: name 'info_table' is not defined